In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LogisticRegression

from sklearn.metrics import balanced_accuracy_score, confusion_matrix, ConfusionMatrixDisplay

from sklearn.pipeline import Pipeline

from sklearn.model_selection import train_test_split

from sklearn.utils.class_weight import compute_class_weight


import joblib

import matplotlib.pyplot as plt
import seaborn as sns
import os

import TrainLR

In [2]:
#Choose input type, one of Rec_Only, Age_Sex, Symptoms, Age_Sex_Symptoms
input_type = 'Rec_Only'

In [3]:
#Define the current working directory, parent and granparent directories
cwd = os.getcwd()
parent_dir = os.path.dirname(cwd)
grandparent_dir = os.path.dirname(parent_dir)

In [4]:
#Load in files used for training
train_files = joblib.load(f'{parent_dir}/FEMH_train_files.pkl')

In [5]:
#Load audio features and remove the file extension from the filename
femh_df = pd.read_csv(f"{grandparent_dir}/Audio Features/FeatureStates_FEMH.csv", index_col=0)
femh_df['filename'] = femh_df['file'].str.split('.', expand=True)[0]
femh_df = femh_df.drop(['file'], axis=1)
femh_df.head()

0         1         2         3         4         5         6  \
0  0.198858 -0.671097 -0.553800  0.430371  0.689427  0.451664  0.513923   
1  0.545076 -0.047681 -1.163096  0.268823  0.509433 -0.136339  0.201685   
2  0.298088 -0.969536 -1.342669  0.438397 -0.010687  0.756730  0.694832   
3  0.297540 -0.991699  2.728217 -0.110462  0.275403  0.368062 -0.597715   
4  0.569070 -0.708248 -0.532420  0.829588  0.291864 -0.042466 -0.483135   

          7         8         9  ...       504       505       506       507  \
0 -0.669326  3.029441 -0.140924  ... -0.467423  0.029338  0.752360 -0.578080   
1 -0.742708 -0.094480  0.041155  ...  1.091321 -0.360934  0.273519 -0.935269   
2  2.412334  0.193469  2.678018  ... -1.588670 -1.013131  0.818641  4.835070   
3 -0.435604  6.930976 -0.512924  ... -1.465304 -1.550032  0.370240  0.287871   
4 -1.057416  2.885130  0.608033  ...  1.912285  1.891305  0.523399 -0.637222   

        508       509       510       511  pathology         filename  
0  1.039529  0.202895  1.363360  0.883992    Atrophy  Atrophy-00002mg  
1 -0.079642 -0.262875 -0.492177  0.851083    Atrophy  Atrophy-0001297  
2 -0.309830  0.503137  1.045041  0.546520    Atrophy  Atrophy-0001apo  
3  1.318349  0.779946  2.578023  0.359360    Atrophy  Atrophy-0001qd3  
4  0.400236  0.318714 -0.948448  0.026111    Atrophy  Atrophy-0002ipt  

[5 rows x 514 columns]

In [6]:
#Load in recording demographics and symptoms
demographics = pd.read_pickle(f'{grandparent_dir}/Audio Demographics/FEMH_demographics.pkl')
demographics.head()

ID Sex Age Disease category Narrow pitch range Decreased volume  \
0  00002mg   1  97        3.Atrophy                  0                0   
1  0001297   1  86        3.Atrophy                  0                0   
2  0001apo   2  45        3.Atrophy                  0                0   
3  0001qd3   1  75        3.Atrophy                  1                1   
4  0002ipt   1  64        3.Atrophy                  0                0   

  Fatigue Dryness Lumping Heartburn  ... Occupational vocal demand Diabetes  \
0       0       0       0         0  ...                         2        0   
1       0       0       0         0  ...                         4        0   
2       0       1       0         0  ...                         3        0   
3       0       0       1         0  ...                         3        0   
4       0       1       0         0  ...                         2        0   

  Hypertension CAD  Head and Neck Cancer Head injury  CVA  \
0            0   0                     0           0    0   
1            1   0                     0           0    1   
2            0   0                     0           0    0   
3            0   1                     0           0    0   
4            0   1                     0           0    0   

  Voice handicap index - 10 pathology         filename  
0                        12   Atrophy  Atrophy-00002mg  
1                        36   Atrophy  Atrophy-0001297  
2                        16   Atrophy  Atrophy-0001apo  
3                        19   Atrophy  Atrophy-0001qd3  
4                        34   Atrophy  Atrophy-0002ipt  

[5 rows x 30 columns]

In [7]:
#Combines the demographics and audio features based on the input type and replaces the pathologies with either malignant or benign
train_df = TrainLR.format_input_dataframe(femh_df, demographics, train_files, input_type=input_type)
print(train_df.shape)
train_df.head()

(1340, 514)


0         1         2         3         4         5         6  \
0  0.198858 -0.671097 -0.553800  0.430371  0.689427  0.451664  0.513923   
1  0.545076 -0.047681 -1.163096  0.268823  0.509433 -0.136339  0.201685   
2  0.297540 -0.991699  2.728217 -0.110462  0.275403  0.368062 -0.597715   
3  0.569070 -0.708248 -0.532420  0.829588  0.291864 -0.042466 -0.483135   
4  0.195015 -0.902380 -0.700360  0.338424  0.612395  0.594198  0.045864   

          7         8         9  ...       504       505       506       507  \
0 -0.669326  3.029441 -0.140924  ... -0.467423  0.029338  0.752360 -0.578080   
1 -0.742708 -0.094480  0.041155  ...  1.091321 -0.360934  0.273519 -0.935269   
2 -0.435604  6.930976 -0.512924  ... -1.465304 -1.550032  0.370240  0.287871   
3 -1.057416  2.885130  0.608033  ...  1.912285  1.891305  0.523399 -0.637222   
4 -1.305794  2.438155  0.677440  ... -0.558422  3.443880  0.061292 -1.131177   

        508       509       510       511  pathology         filename  
0  1.039529  0.202895  1.363360  0.883992     Benign  Atrophy-00002mg  
1 -0.079642 -0.262875 -0.492177  0.851083     Benign  Atrophy-0001297  
2  1.318349  0.779946  2.578023  0.359360     Benign  Atrophy-0001qd3  
3  0.400236  0.318714 -0.948448  0.026111     Benign  Atrophy-0002ipt  
4  1.715775  0.550369  1.798784 -0.572442     Benign  Atrophy-0002m5r  

[5 rows x 514 columns]

In [8]:
#Separate features and target
X_train = train_df.drop(['pathology', 'filename'], axis=1)
y_train = train_df['pathology']

In [9]:
X_train.shape

(1340, 512)

In [10]:
#Define the audio features
audio_features = femh_df.columns.drop(['pathology', 'filename'])
audio_features

Index(['0', '1', '2', '3', '4', '5', '6', '7', '8', '9',
       ...
       '502', '503', '504', '505', '506', '507', '508', '509', '510', '511'],
      dtype='object', length=512)

In [11]:
#Define the symptom and demographic features if any
symptom_features = X_train.columns.drop(audio_features)
symptom_features

Index([], dtype='object')

In [12]:
preprocessor = TrainLR.create_preprocessor(audio_features, symptom_features)

In [13]:
# Compute class weights
class_weights = compute_class_weight(class_weight='balanced', classes=np.unique(y_train), y=y_train)

# Create a dictionary mapping the class labels to their weights
class_weight_dict = {cls: weight for cls, weight in zip(np.unique(y_train), class_weights)}
class_weight_dict

{'Benign': 0.5134099616858238, 'Malignant': 19.142857142857142}

In [14]:
#Create a pipeline for the preprocessing and classifier
pipeline = Pipeline(steps=[
('preprocessor', preprocessor),
('classifier', LogisticRegression(random_state=42, class_weight=class_weight_dict))
])

In [15]:
param_grid = {
    'classifier__penalty': ['l1', 'l2', 'elasticnet', None],        # Regularization penalty
    'classifier__C': [0.01, 0.1, 1, 10, 100],                       # Inverse of regularization strength
    'classifier__solver': ['newton-cg', 'lbfgs', 'liblinear', 'saga'],  # Algorithm to use in the optimization problem
    'classifier__max_iter': [100, 200, 300, 500],                   # Maximum number of iterations to converge
    'classifier__l1_ratio': [0, 0.25, 0.5, 0.75, 1]                 # Elastic-Net mixing parameter (only used if penalty is 'elasticnet')
}

In [16]:
# Initialize GridSearchCV with 5 folds
grid_search = GridSearchCV(estimator=pipeline, param_grid=param_grid, cv=5, scoring='balanced_accuracy', verbose=3, return_train_score=True)

In [23]:
# Fit the classifier using the training data
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 1600 candidates, totalling 8000 fits
[CV 1/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=newton-cg;, score=(train=nan, test=nan) total time=   0.9s
[CV 2/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=newton-cg;, score=(train=nan, test=nan) total time=   0.8s
[CV 3/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=newton-cg;, score=(train=nan, test=nan) total time=   1.0s
[CV 4/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=newton-cg;, score=(train=nan, test=nan) total time=   1.0s
[CV 5/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=newton-cg;, score=(train=nan, test=nan) total time=   0.5s
[CV 1/5] E

D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\linear_model\_logistic.py:1175: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(


[CV 1/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=liblinear;, score=(train=0.803, test=0.687) total time=   0.9s


D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\linear_model\_logistic.py:1175: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(


[CV 2/5] END classifier__C=0.01, classifier__l1_ratio=0, classifier__max_iter=100, classifier__penalty=l1, classifier__solver=liblinear;, score=(train=0.811, test=0.761) total time=   0.8s


...

[CV 4/5] END classifier__C=100, classifier__l1_ratio=1, classifier__max_iter=500, classifier__penalty=None, classifier__solver=saga;, score=(train=0.933, test=0.800) total time=   1.1s


D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\linear_model\_logistic.py:1175: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=None)
  warnings.warn(
D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\linear_model\_logistic.py:1186: UserWarning: Setting penalty=None will ignore the C and l1_ratio parameters
  warnings.warn(
D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\linear_model\_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\model_selection\_validation.py:547: FitFailedWarning: 
3000 fits failed out of a total of 8000.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
-

[CV 5/5] END classifier__C=100, classifier__l1_ratio=1, classifier__max_iter=500, classifier__penalty=None, classifier__solver=saga;, score=(train=0.910, test=0.654) total time=   0.6s


D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\model_selection\_search.py:1051: UserWarning: One or more of the test scores are non-finite: [       nan        nan 0.73902573 ... 0.69939792        nan 0.67400109]
  warnings.warn(
D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\model_selection\_search.py:1051: UserWarning: One or more of the train scores are non-finite: [       nan        nan 0.79404762 ... 0.93389436        nan 0.91034483]
  warnings.warn(
D:\Users\maryp\anaconda3\envs\speech_commands\Lib\site-packages\sklearn\linear_model\_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocessor',
                                        ColumnTransformer(transformers=[('audio',
                                                                         Pipeline(steps=[('imputer',
                                                                                          SimpleImputer()),
                                                                                         ('scaler',
                                                                                          StandardScaler()),
                                                                                         ('feature_selection',
                                                                                          SelectFromModel(estimator=DecisionTreeClassifier(random_state=42)))]),
                                                                         Index(['0', '1', '2', '3', '4', '5', '6', '7', '8', '9',
       ...
       '502', '503', '504', '505', '506', '507',...
                                                                         'Malignant': 19.142857142857142},
                                                           random_state=42))]),
             param_grid={'classifier__C': [0.01, 0.1, 1, 10, 100],
                         'classifier__l1_ratio': [0, 0.25, 0.5, 0.75, 1],
                         'classifier__max_iter': [100, 200, 300, 500],
                         'classifier__penalty': ['l1', 'l2', 'elasticnet',
                                                 None],
                         'classifier__solver': ['newton-cg', 'lbfgs',
                                                'liblinear', 'saga']},
             return_train_score=True, scoring='balanced_accuracy', verbose=3)

In [24]:
# Best parameters from GridSearchCV
print(f'Best parameters: {grid_search.best_params_}')

# Best estimator from GridSearchCV
best_pipeline = grid_search.best_estimator_

Best parameters: {'classifier__C': 0.1, 'classifier__l1_ratio': 0.25, 'classifier__max_iter': 100, 'classifier__penalty': 'elasticnet', 'classifier__solver': 'saga'}


In [25]:
cv_results = grid_search.cv_results_

best_index = grid_search.best_index_
print("Cross-validation results for the best parameters:")

print(f"Mean test score: {cv_results['mean_test_score'][best_index]}")
print(f"Mean train score: {cv_results['mean_train_score'][best_index]}")

Cross-validation results for the best parameters:
Mean test score: 0.7911877394636015
Mean train score: 0.8515736179529283


In [26]:
joblib.dump(grid_search, f'{grandparent_dir}/Pre-Trained Models/LR_FeatureStates_{input_type}.pkl', compress=True)

['LR_FeatureStates_Age_Sex.pkl']